In [243]:
# importing library
import matplotlib.pyplot as plt
import pandas as pd
import csv

In [178]:
def create_transaction_dictonary(transactions):
    transactions_list = transactions.values.tolist()
    Id = 0
    transactions_dict = {tx[Id] for tx in transactions_list}
    return transactions_dict
        

In [179]:
def find_block_id(tx_id):
    row = transactions.loc[transactions['id'] == tx_id]
    block_id = row['block_id'].values[0]
    return block_id

In [180]:
def eliminate_invalid_transactions(no_valid_transactions):
    for tx in no_valid_transactions:
        inputs.drop(inputs.index[inputs['tx_id'] == tx], inplace=True)
        outputs.drop(outputs.index[outputs['tx_id'] == tx], inplace=True)
        transactions.drop(transactions.index[transactions['id'] == tx], inplace=True)
        
    print("INVALID TRANSACTION ELIMINATED")


In [181]:
def eliminate_descendent_transaction():
    #output_of_transaction_to_drop = {}
#for i in range(0, len(transaction_to_drop)):
#    outputs_of_eliminated_transaction = outputs.loc[outputs['tx_id']== transaction_to_drop[i]]
#    list_output_id = outputs_of_eliminated_transaction['id'].tolist()
#    output_of_transaction_to_drop[transaction_to_drop[i]] = list_output_id    

#for key in output_of_transaction_to_drop:
#    print(key, '->', output_of_transaction_to_drop[key]) 
#print("\n")
    
#transaction_to_drop = [61845,207365,12152, 30446]
#for i in range(0, len(transaction_to_drop)):
#    inputs.drop(inputs.index[inputs['tx_id'] == transaction_to_drop[i]], inplace=True)
#    outputs.drop(outputs.index[outputs['tx_id'] == transaction_to_drop[i]], inplace=True)
#    transactions.drop(transactions.index[transactions['id'] == transaction_to_drop[i]], inplace=True)


#I verify that the output of these transactions that need to be eliminated is not present as an input for subsequent transactions. 
#(Process repeated in cascade also for subsequent transactions)
#discendent_transaction = {61845:[], 207365: [], 12152:[], 30446:[]}
#input_dictionary_with_o_id_key =  create_inputs_dictionary_with_key_output_id(inputs)
#outputs_list = outputs.values.tolist()


#check if the output of the eliminated transactions is used
#for key in output_of_transaction_to_drop:
#    list_output = output_of_transaction_to_drop[key]
#    for i in range(0, len(list_output)):
#        if list_output[i] in input_dictionary_with_o_id_key:
#            print("Output with id " + str(list_output[i]) + " of the eliminated transaction with id: " + str(key) + " is used in another transaction")
#        else:
#            print("Output with id " + str(list_output[i]) + " of the eliminated transaction with id: " + str(key) + " is not used in another transaction")


#find all the descendants transactions
#outputs_id_to_check = [249865]
#transaction_id_to_eliminate = []
#while len(outputs_id_to_check) > 0:
#    output_id = outputs_id_to_check.pop()
#    result = inputs.loc[inputs['output_id'] == output_id]
#    result_list = result['tx_id'].tolist()
#    transaction_id_to_eliminate.extend(result_list)
#    for tx in result_list:
#        second_query = outputs.loc[outputs['tx_id']== tx]
#       outputs_id_to_test = second_query["id"].tolist()
#        for o in outputs_id_to_test:
#            outputs_df_used = inputs.loc[inputs['output_id'] == o]
#            outputs_list_used = outputs_df_used['output_id'].tolist()
#            outputs_id_to_check.extend(outputs_list_used)
            
#print(len(transaction_id_to_eliminate))
#print(transaction_id_to_eliminate)


SyntaxError: unexpected EOF while parsing (<ipython-input-181-1ec4a78b879c>, line 53)

In [182]:
def check_output_of_invalid_transactions(no_valid_transactions):
    is_used = False
    somma = 0
    for element in no_valid_transactions:
        output_df = outputs.loc[outputs['tx_id']== element]
        output_id_list = output_df['id'].tolist()
        for Id in output_id_list:
            input_df = inputs.loc[inputs['output_id']== Id]
            tx_list = input_df['tx_id'].tolist()
            if len(tx_list) > 0:
                is_used = True
    if is_used:
        print("The transaction outputs to be deleted are used as inputs for other transactions\n")
    else:
        print("The transaction outputs to be deleted are not used as inputs for other transactions\n")


In [183]:
def select_transactions_to_eliminate(inputs_with_double_output_id, inputs, outputs):
    inputs_list = inputs_with_double_output_id.values.tolist()
    no_valid_transaction = [] 
    o_id = 3
    tx_id = 1
    founded = False
    for element in inputs_list:
        transaction_id = element[tx_id]
        output_id = element[o_id]
        #print(output_id)
        #it is necessary to verify that the tx_id of the transaction that produced this output is 
        #less than the current tx_id, if this is not the case it means that this transaction is using 
        #an output_id that has been produced in the future, this means that the current transaction is not valid
        outputs_row = outputs.loc[outputs['id']== output_id] 
        outputs_row_list = outputs_row.values.tolist()
        tx_id_output = outputs_row_list[0][tx_id]
        if tx_id_output > transaction_id:
            no_valid_transaction.append(transaction_id)
            founded = True

    #if the test is passed by all the transactions then I decide to consider the transaction with 
    #lower tx_id valid
    if not founded:
        valid_tx = inputs_with_double_output_id['tx_id'].min()
        tx = inputs_with_double_output_id['tx_id'].values.tolist()
        tx.remove(valid_tx)
        return tx
    
    return no_valid_transaction

In [184]:
def create_inputs_dictionary_with_key_output_id(inputs):
    inputs_list = inputs.values.tolist()
    output_id = 3
    input_dict_with_o_key = {}
    #input_dict_with_o_key = {tx[output_id] for tx in inputs_list}
    for tx in inputs_list:
        input_dict_with_o_key[tx[output_id]] = True
        
    return input_dict_with_o_key

In [185]:
def create_sum_input_by_tx_id_dictionary(outputs_dict, inputs_list):
    sum_input_value_per_transaction = {}
    transaction_id = 1 # indice dell'id della transazione nella singola tupla appartentente a input_list
    output_id = 3
    for i in range(0, len(inputs_list)):
        tx_id = inputs_list[i][transaction_id]
        o_id = inputs_list[i][output_id]
        
        if (o_id == -1):
            sum_input_value_per_transaction[tx_id] = -1
            continue
        
        if tx_id not in sum_input_value_per_transaction:
            sum_input_value_per_transaction[tx_id] = outputs_dict.get(o_id)
        else:
            sum_input_value_per_transaction[tx_id] += outputs_dict.get(o_id)
      
    return sum_input_value_per_transaction
        
    

In [186]:
def create_output_dictionary(outputs_list):
    output_dict = {}
    output_id = 0 #indice dell'output_id nella tupla
    output_value = 3 #indice dell'output_value nella tupla
    for i in range(0, len(outputs_list)):
        output_dict[outputs_list[i][output_id]] = outputs_list[i][output_value]
    
    return output_dict


In [187]:
def create_sum_output_by_tx_id_dictionary(outputs_list):
    sum_output_value_per_transaction = {}
    transaction_id = 1# indice dell'id della transazione nella singola tupla appartentente a output_list
    output_value = 3 #indice dell'output value nella singola tupla appartentente a output_list
    for i in range(0, len(outputs_list)):
        tx_id = outputs_list[i][transaction_id]
        if tx_id in sum_output_value_per_transaction:
            sum_output_value_per_transaction[tx_id] += outputs_list[i][output_value]
        else:
            sum_output_value_per_transaction[tx_id] = outputs_list[i][output_value]
        
    return sum_output_value_per_transaction
    

In [188]:
#reading .csv file
transactions = pd.read_csv('./data_with_header/transactions.csv', index_col=False)
inputs = pd.read_csv('./data_with_header/inputs.csv', index_col=False)
outputs = pd.read_csv('./data_with_header/outputs.csv', index_col=False)
dates = pd.read_csv('./data_with_header/dates.csv', index_col=False)

In [189]:
inputs.loc[inputs['output_id'] == 264307]

Empty DataFrame
Columns: [id, tx_id, sig_id, output_id]
Index: []

In [190]:
outputs.loc[outputs['id']== 2862]

id  tx_id  pk_id       value
2861  2862   2850   2841  4999000000

In [213]:
outputs.loc[outputs['tx_id']== 216623]
outputs.groupby('pk_id').count()


id  tx_id  value
pk_id                    
-10       3      3      3
 1        1      1      1
 2        1      1      1
 3        1      1      1
 4        1      1      1
...      ..    ...    ...
 174697   1      1      1
 174698   1      1      1
 174699   1      1      1
 174700   1      1      1
 174701   2      2      2

[174702 rows x 3 columns]

In [192]:
print(transactions['id'].is_unique)

True


## FIRST PART: 
### 1) Describe how a real Bitcoin transaction is abstracted by a transaction in  the dataset (which fields are eliminated, which are abstracted and how).


DA FARE


## 2) Check if all the data contained in the dataset is consistent, and if some data is invalid, describe what is the problem of that data and remove it from the dataset.

In [193]:
print("--------CHECK IF OUTPUT_ID IN INPUTS.CSV IS UNIQUE--------\n")
#quinta verifica: controllare che ad ogni output_id nel file di inputs corrisponda un solo id nel file di outputà
#print(outputs['id'].is_unique)

o_input = inputs['output_id'].value_counts()
o_input_frame = o_input.to_frame()
no_valid_transactions = []

print("output_id with the number of occurrences that appear in the input.csv file")
o_input_frame = o_input_frame.rename(columns={'': 'output_id', 'output_id': 'count'})
o_input_frame_filtered =  o_input_frame.query('count >= 2')
print(o_input_frame_filtered)
print("\n")

output_used_twice = o_input_frame_filtered.index.values.tolist()

for element in output_used_twice:
    if element == -1:
        output_used_twice.remove(element)

print("The output ids that have been used more than once are") 
print(output_used_twice)
print("We can see that the output with id = -1 is not considered because it denotes a coinbase transaction\n")


print("Input row with output_id that have the problems of double spending")
for i in range(0, len(output_used_twice)):
    inputs_with_double_output_id = inputs.loc[inputs['output_id'] == output_used_twice[i]]
    print(inputs_with_double_output_id)
    print("\n")
    transactions_to_eliminate = select_transactions_to_eliminate(inputs_with_double_output_id, inputs, outputs)
    no_valid_transactions.extend(transactions_to_eliminate)

print("The following tx_id are not valid: " + str(no_valid_transactions))
print("\n")

print("You must ensure that the output that is produced by these eliminated transactions is not being used as input for subsequent transactions.\n")

check_output_of_invalid_transactions(no_valid_transactions)
eliminate_invalid_transactions(no_valid_transactions)


--------CHECK IF OUTPUT_ID IN INPUTS.CSV IS UNIQUE--------

output_id with the number of occurrences that appear in the input.csv file
          count
-1       100018
 65403        2
 249860       2
 7998         2
 21928        2


The output ids that have been used more than once are
[65403, 249860, 7998, 21928]
We can see that the output with id = -1 is not considered because it denotes a coinbase transaction

Input row with output_id that have the problems of double spending
          id  tx_id  sig_id  output_id
76746  76747  61843  138980      65403
76749  76750  61845  138980      65403


            id   tx_id  sig_id  output_id
275613  275614  204751  163625     249860
279608  279609  207365  163625     249860


          id  tx_id  sig_id  output_id
8665    8666   8231    7941       7998
12819  12820  12152    7941       7998


          id  tx_id  sig_id  output_id
33112  33113  30446   21807      21928
33113  33114  30446   21807      21928


The following tx_id are not val

In [194]:
#first check: verify that the tx_id that appears in the inputs.csv file is a valid one considering the tx_id in the transactions.csv file
print("--------CHECK IF IF TX_ID IN INPUT.CSV IS VALID--------")
transactions_dict = create_transaction_dictonary(transactions)
inputs_list = inputs.values.tolist()
outputs_list = outputs.values.tolist()
transactions_list = transactions.values.tolist()  
contatore = 0
for i in range(0, len(inputs_list)):
    if (inputs_list[i][1] not in transactions_dict):
        contatore = contatore + 1
if(contatore == 0):
    print("Test passed")

--------CHECK IF IF TX_ID IN INPUT.CSV IS VALID--------
Test passed


In [195]:
print("--------CHECK IF IF TX_ID IN OUTPUT.CSV IS VALID--------")
#second check: verify that the tx_id that appears in the outputs.csv file is a valid one considering the tx_id in the transactions.csv file
contatore = 0
for i in range(0, len(outputs_list)):
    if (outputs_list[i][1] not in transactions_dict):
        contatore = contatore + 1
if(contatore == 0):
    print("Test passed")

--------CHECK IF IF TX_ID IN OUTPUT.CSV IS VALID--------
Test passed


In [196]:
print("--------CHECK IF IF OUTPUT_ID IN INPUT.CSV IS VALID--------")
#terza verifica: verifica che l'output_id che appare nel file di input.csv sia un output_id valido,
#ossia che sia presente nel file output.csv, per avere un accesso diretto al file di output, lo trasformo in un dizionario
output_dict = create_output_dictionary(outputs_list)
inputs_list = inputs.values.tolist()
output_id = 3 #indice dell'output_id nella singola tupla di input_list
tx_id = 1
no_valid_transactions = []

for i in range(0, len(inputs_list)):
    if(inputs_list[i][output_id] == -1):
        continue #is coinbase transaction
        
    if (inputs_list[i][output_id] not in output_dict):
        no_valid_transactions.append(inputs_list[i][tx_id])
        print('Invalid tx_id: ' + str(inputs_list[i][1]))
        print('Output_id that does not exist: ' + str(inputs_list[i][output_id]))
        print('Invalid transaction input_id: ' + str(inputs_list[i][0]))
        print("\n")

print("Transactions_id with inputs that don't have a valid output_id are: " + str(no_valid_transactions) + "\n")

print("You must ensure that the output that is produced by these eliminated transactions is not being used as input for subsequent transactions.\n")
check_output_of_invalid_transactions(no_valid_transactions)

eliminate_invalid_transactions(no_valid_transactions)


    

--------CHECK IF IF OUTPUT_ID IN INPUT.CSV IS VALID--------
Invalid tx_id: 15698
Output_id that does not exist: 265834
Invalid transaction input_id: 16461


Transactions_id with inputs that don't have a valid output_id are: [15698]

You must ensure that the output that is produced by these eliminated transactions is not being used as input for subsequent transactions.

The transaction outputs to be deleted are not used as inputs for other transactions

INVALID TRANSACTION ELIMINATED


In [172]:
print("--------CHECK FOR FOR EACH IF THE SUM OF INPUT > SUM OF OUTPUT--------\n")
no_valid_transactions = []
transactions_dict = create_transaction_dictonary(transactions)
inputs_list = inputs.values.tolist()
outputs_list = outputs.values.tolist()
transactions_list = transactions.values.tolist()  
output_dict = create_output_dictionary(outputs_list)

#quarta verifica: verifica che la somma dell'input sia maggiore della somma dell'output
sum_output_value_per_transaction = create_sum_output_by_tx_id_dictionary(outputs_list)
sum_input_value_per_transaction = create_sum_input_by_tx_id_dictionary(output_dict, inputs_list)
transaction_id = 0 #indice della tupla nella singola transazione della lista transactions_list

for i in range(0, len(transactions_list)):
    tx_id = transactions_list[i][transaction_id]
    
    output_value = sum_output_value_per_transaction.get(tx_id)
    input_value = sum_input_value_per_transaction.get(tx_id)
    if(input_value == -1):
        continue #coinbase transaction
    if(output_value > input_value):
        contatore +=1
        no_valid_transactions.append(tx_id)

print("Transactions to be eliminated that have the output value greater than the input value are: " + str(no_valid_transactions) + "\n")
print("You must ensure that the output that is produced by these eliminated transactions is not being used as input for subsequent transactions.\n")
check_output_of_invalid_transactions(no_valid_transactions)

eliminate_invalid_transactions(no_valid_transactions)



--------CHECK FOR FOR EACH IF THE SUM OF INPUT > SUM OF OUTPUT--------

Transactions to be eliminated that have the output value greater than the input value are: [100929]

You must ensure that the output that is produced by these eliminated transactions is not being used as input for subsequent transactions.

The transaction outputs to be deleted are not used as inputs for other transactions

INVALID TRANSACTION ELIMINATED


In [208]:
print("--------CHECK IT THERE ARE ANY MISSING BLOCKS_IDS--------\n")
#The blocks_id are consecutive (they starts with block_id = 0 up to its maximum value). 
#This test verifies that there are no missing values in the sequence (0, MAX (block_id)
missing_blocks_id = []
blocks_id_list = (transactions.block_id.unique()).tolist()
for i in range(0, len(blocks_id_list)-1):
    if blocks_id_list[i+1] != blocks_id_list[i] + 1:
        missing_blocks_id.append(blocks_id_list[i] + 1)
print("Missing blocks_id are: " + str(missing_blocks_id))

--------CHECK IT THERE ARE ANY MISSING BLOCKS_IDS--------

Missing blocks_id are: [91857]


## 3) Compute the total amount of UTXOs (Unspent Transaction Outputs) existing as of the last block of the data set, i.e. the sum of all the Transaction outputs balances on the UTXO set of the last block. Which UTXO (TxId, blockId, output index and address) has the highest asso- ciated value?

In [174]:
#creating a dictionary of the input.csv file using the output_id as a key. 
#This way I check with a single access to the dictionary if a specific output id has been spent
max_uxto_tx_id = 0
max_uxto_block_id = 0
max_uxto_output_id = 0
max_uxto_address = 0
max_uxto_value = 0
total_uxto = 0

outputs_list = outputs.values.tolist()
output_id = 0
value_index = 3
tx_index = 1
address_index = 2
input_dictionary_with_o_id_key =  create_inputs_dictionary_with_key_output_id(inputs)

for element in outputs_list:
    o_id = element[output_id]
    output_value = element[value_index]
    if o_id not in input_dictionary_with_o_id_key:
        total_uxto += output_value
        if output_value > max_uxto_value:
            max_uxto_tx_id = element[tx_index]
            max_uxto_output_id = o_id
            max_uxto_address = element[address_index]
            max_uxto_value = output_value
            max_uxto_block_id = find_block_id(element[tx_index])

print("The total amount of UTXOs existing as of the last block of the data set is: " + str(total_uxto) + "\n")

print("Max UXTO:")
print("\ttx_id: " + str(max_uxto_tx_id))
print("\tblock_id: " + str(max_uxto_block_id))
print("\toutput_id: " + str(max_uxto_output_id))
print("\taddress: " + str(max_uxto_address))
print("\tvalue: " + str(max_uxto_value))


The total amount of UTXOs existing as of the last block of the data set is: 500074833333344

Max UXTO:
	tx_id: 140479
	block_id: 90532
	output_id: 170430
	address: 138895
	value: 9000000000000


## 4) The distribution of the block occupancy, i.e. of the number of trans- actions in each block in the entire period of time. Furthermore, show the evolution in time of the block size, by considering a time step of one month.

In [210]:
#creation of dataframe with transaction number contained within each block
transaction_per_block = transactions.groupby('block_id').count()
transaction_per_block.rename(columns = {'id':'n_tx'}, inplace = True)
block_id_list = transaction_per_block.index.values.tolist()   
n_tx_per_block_list = transaction_per_block['n_tx'].tolist()
transaction_per_block = pd.DataFrame(list(zip(block_id_list, n_tx_per_block_list )), columns = ['block_id', 'n_tx'])
transaction_per_block


dates_list = dates.values.tolist()
only_year_month = []
list_block_id = []

#I remove the time and day from the time column since what we are interested in is to 
#see the number of transactions in a month
block_index = 0
date_index = 1
for i in range(0, len(dates_list)):
    if (dates_list[i][block_index] not in missing_blocks_id ):
        date = dates_list[i][date_index][0:7:1]
        only_year_month.append(date)
        list_block_id.append(dates_list[i][block_index] )
    else:
        print("saltato")

blocks_with_date = pd.DataFrame(list(zip(list_block_id, only_year_month )), columns = ['block_id', 'date'])

block_tx_with_date = transaction_per_block.merge(blocks_with_date, on='block_id')
transaction_per_month = block_tx_with_date.groupby(['date'])['n_tx'].sum()
transaction_per_month


saltato


date
2009-01     2576
2009-02     3417
2009-03     3490
2009-04     3460
2009-05     3401
2009-06     2244
2009-07     1930
2009-08     1570
2009-09     2170
2009-10     2139
2009-11     2232
2009-12     4084
2010-01     5056
2010-02     5751
2010-03     5398
2010-04     9633
2010-05     6217
2010-06     6684
2010-07    26485
2010-08    11968
2010-09    13183
2010-10    14393
2010-11    63409
2010-12    15731
Name: n_tx, dtype: int64

In [325]:
#write information aboute transctions per block  in month_tx.csv file.

list_of_month = transaction_per_month.index.values.tolist() 
value = transaction_per_month.tolist()


f = open('month_tx.csv', 'w')
writer = csv.writer(f)
header = ['month', 'tot_tx']
writer.writerow(header)
for i in range  (0,len(list_of_month)):
    row = []
    row.append(list_of_month[i])
    row.append(value[i])
    writer.writerow(row)
f.close()

In [176]:
to_check = inputs.loc[inputs['output_id'] == -1]
tx_id_to_check = to_check['tx_id']
list_tx = tx_id_to_check.values.tolist()
tx_to_check = []
for tx in list_tx:
    o_rows = outputs.loc[outputs['tx_id'] == tx]
    total = o_rows['value'].sum()
    if(total != 5000000000):
        tx_to_check.append(tx)

print(tx_to_check)
        

KeyboardInterrupt: 

## 5) The total amount of bitcoin received from each public key that has received at least one COINBASE transaction, in the considered period, and show a distribution of the values

In [242]:
pk_coinbase_value_dict = {}
coinbase_transaction_df = inputs.loc[inputs['output_id']== -1]
coinbase_tx_list = coinbase_transaction_df['tx_id'].tolist()

pk_id_index = 2
value_index = 3
for i in range(0, len(coinbase_tx_list)):
    df_output_coinbase = outputs.loc[outputs['tx_id']== coinbase_tx_list[i]]
    df_output_coinbase_list = df_output_coinbase.values.tolist()
    for j in range(0, len(df_output_coinbase_list)):
        pk_id = df_output_coinbase_list[j][pk_id_index]
        value = df_output_coinbase_list[j][value_index]
        if pk_id not in pk_coinbase_value_dict:
            pk_coinbase_value_dict[pk_id] = value
        else:
            pk_coinbase_value_dict[pk_id] += value



{1: 5000000000, 2: 5000000000, 3: 5000000000, 4: 5000000000, 5: 5000000000, 6: 5000000000, 7: 5000000000, 8: 5000000000, 9: 5000000000, 10: 5000000000, 11: 5000000000, 12: 5000000000, 13: 5000000000, 14: 5000000000, 15: 5000000000, 16: 5000000000, 17: 5000000000, 18: 5000000000, 19: 5000000000, 20: 5000000000, 21: 5000000000, 22: 5000000000, 23: 5000000000, 24: 5000000000, 25: 5000000000, 26: 5000000000, 27: 5000000000, 28: 5000000000, 29: 5000000000, 30: 5000000000, 31: 5000000000, 32: 5000000000, 33: 5000000000, 34: 5000000000, 35: 5000000000, 36: 5000000000, 37: 5000000000, 38: 5000000000, 39: 5000000000, 40: 5000000000, 41: 5000000000, 42: 5000000000, 43: 5000000000, 44: 5000000000, 45: 5000000000, 46: 5000000000, 47: 5000000000, 48: 5000000000, 49: 5000000000, 50: 5000000000, 51: 5000000000, 52: 5000000000, 53: 5000000000, 54: 5000000000, 55: 5000000000, 56: 5000000000, 57: 5000000000, 58: 5000000000, 59: 5000000000, 60: 5000000000, 61: 5000000000, 62: 5000000000, 63: 5000000000, 

In [252]:
print(coinbase_transaction_df['tx_id'].is_unique)


True


In [ ]:
#inserire codice per scrivere nel file csv il dictionary reward

In [255]:
total_transactions = len(transactions)
coinbase_transactions = len(coinbase_tx_list)
print('Total number of transactions in the dataset: ' + str(total_transactions))
print('Total number of coinbase transactions in the dataset: ' + str(coinbase_transactions))


Total number of transactions in the dataset: 216621
Total number of coinbase transactions in the dataset: 100018


## 6) The distribution of the fees spent in each transaction in the considered period.


In [268]:

transactions_dict = create_transaction_dictonary(transactions)
inputs_list = inputs.values.tolist()
outputs_list = outputs.values.tolist()
transactions_list = transactions.values.tolist()  
output_dict = create_output_dictionary(outputs_list)
max_fees_value = 0
max_tx = 0
sum_output_value_per_transaction = create_sum_output_by_tx_id_dictionary(outputs_list)
sum_input_value_per_transaction = create_sum_input_by_tx_id_dictionary(output_dict, inputs_list)
transaction_id = 0 #indice della tupla nella singola transazione della lista transactions_list
transactions_block_id = 1 #index of the block_id 
transactions_with_fees = []
for i in range(0, len(transactions_list)):
    tx_id = transactions_list[i][transaction_id]
    block_id = transactions_list[i][transactions_block_id]
    output_value = sum_output_value_per_transaction.get(tx_id)
    input_value = sum_input_value_per_transaction.get(tx_id)
    if(input_value == -1):
        continue #coinbase transaction
    if(input_value > output_value):
        fees = input_value - output_value
        if fees > max_fees_value:
            max_fees_value = fees
            max_tx = tx_id
        coinbase_transaction = [tx_id, block_id, input_value, output_value, fees]
        transactions_with_fees.append(coinbase_transaction)

print("Number of transactions with fees: " + str(len(transactions_with_fees)))
print("Transaction with max fees:")
print("\tTransaction Id: " + str(max_tx))
print("\tValue of the fees: " + str(max_fees_value))



Number of transactions with fees: 1301
Transaction with max feed:
	Transaction Id: 105281
	Value of the fees: 10000000000


In [267]:
#write information aboute transactions fees in transactions_with_fee.csv file.
f = open('transactions_with_fee.csv', 'w')
writer = csv.writer(f)
header = ['tx_id', 'block_id', 'total_input', 'total_output', 'fees'] 
writer.writerow(header)
for i in range  (0, len(transactions_with_fees)):
    writer.writerow(transactions_with_fees[i])

f.close()

In [270]:
10000000000 / 20

500000000.0

In [281]:
step = int(max_fees_value/20)
min_limit = 0
max_limit = step

value_index = 4
range_dict = {}
while min_limit < max_fees_value:
    key = str(min_limit) + "-" + str(max_limit)
    range_dict[key] = 0
    for i in range(0, len(transactions_with_fees)):
        value = transactions_with_fees[i][value_index]
        if(min_limit < value and value <= max_limit):
            range_dict[key] += 1

    min_limit = max_limit
    max_limit += step
    
for key in range_dict:
    print(str(key) + "->" + str(range_dict.get(key)))

0-500000000->1298
500000000-1000000000->0
1000000000-1500000000->0
1500000000-2000000000->0
2000000000-2500000000->0
2500000000-3000000000->0
3000000000-3500000000->0
3500000000-4000000000->0
4000000000-4500000000->0
4500000000-5000000000->2
5000000000-5500000000->0
5500000000-6000000000->0
6000000000-6500000000->0
6500000000-7000000000->0
7000000000-7500000000->0
7500000000-8000000000->0
8000000000-8500000000->0
8500000000-9000000000->0
9000000000-9500000000->0
9500000000-10000000000->1


In [282]:
#write information aboute range transactions fees in fees_range.csv file.
f = open('fees_range.csv', 'w')
writer = csv.writer(f)
header = ['range', 'number_transactions'] 
writer.writerow(header)
for key in range_dict:
    row = [key]
    value = range_dict.get(key)
    row.append(value)
    writer.writerow(row)

f.close()

In [291]:
#Since most transactions have fees in the first range, let's see how the transactions in this range 
#are distributed by further dividing this range into sub ranges
limit = 500000000
step = int(limit / 100000)
min_limit_sub = 0
max_limit_sub = step
value_index = 4
range_dict_sub = {}
while min_limit_sub < limit:
    key = str(min_limit_sub) + "-" + str(max_limit_sub)
    range_dict_sub[key] = 0
    for i in range(0, len(transactions_with_fees)):
        value = transactions_with_fees[i][value_index]
        if(min_limit_sub < value and value <= max_limit_sub):
            range_dict_sub[key] += 1
    
    min_limit_sub = max_limit_sub
    max_limit_sub += step

for key in range_dict_sub:
    print(str(key) + "->" + str(range_dict_sub.get(key)))

0-5000->31
5000-10000->0
10000-15000->0
15000-20000->0
20000-25000->0
25000-30000->0
30000-35000->0
35000-40000->0
40000-45000->0
45000-50000->0
50000-55000->0
55000-60000->0
60000-65000->0
65000-70000->0
70000-75000->0
75000-80000->0
80000-85000->0
85000-90000->0
90000-95000->1
95000-100000->0
100000-105000->0
105000-110000->0
110000-115000->0
115000-120000->0
120000-125000->0
125000-130000->0
130000-135000->0
135000-140000->0
140000-145000->0
145000-150000->0
150000-155000->0
155000-160000->0
160000-165000->0
165000-170000->0
170000-175000->0
175000-180000->0
180000-185000->1
185000-190000->0
190000-195000->1
195000-200000->0
200000-205000->0
205000-210000->0
210000-215000->1
215000-220000->0
220000-225000->0
225000-230000->0
230000-235000->0
235000-240000->0
240000-245000->0
245000-250000->0
250000-255000->0
255000-260000->0
260000-265000->3
265000-270000->1
270000-275000->1
275000-280000->0
280000-285000->1
285000-290000->0
290000-295000->0
295000-300000->0
300000-305000->0
305000-

8515000-8520000->0
8520000-8525000->0
8525000-8530000->0
8530000-8535000->0
8535000-8540000->0
8540000-8545000->0
8545000-8550000->0
8550000-8555000->0
8555000-8560000->0
8560000-8565000->0
8565000-8570000->0
8570000-8575000->0
8575000-8580000->0
8580000-8585000->0
8585000-8590000->0
8590000-8595000->0
8595000-8600000->0
8600000-8605000->0
8605000-8610000->0
8610000-8615000->0
8615000-8620000->0
8620000-8625000->0
8625000-8630000->0
8630000-8635000->0
8635000-8640000->0
8640000-8645000->0
8645000-8650000->0
8650000-8655000->0
8655000-8660000->0
8660000-8665000->0
8665000-8670000->0
8670000-8675000->0
8675000-8680000->0
8680000-8685000->0
8685000-8690000->0
8690000-8695000->0
8695000-8700000->0
8700000-8705000->0
8705000-8710000->0
8710000-8715000->0
8715000-8720000->0
8720000-8725000->0
8725000-8730000->0
8730000-8735000->0
8735000-8740000->0
8740000-8745000->0
8745000-8750000->0
8750000-8755000->0
8755000-8760000->0
8760000-8765000->0
8765000-8770000->0
8770000-8775000->0
8775000-8780

16015000-16020000->0
16020000-16025000->0
16025000-16030000->0
16030000-16035000->0
16035000-16040000->0
16040000-16045000->0
16045000-16050000->0
16050000-16055000->0
16055000-16060000->0
16060000-16065000->0
16065000-16070000->0
16070000-16075000->0
16075000-16080000->0
16080000-16085000->0
16085000-16090000->0
16090000-16095000->0
16095000-16100000->0
16100000-16105000->0
16105000-16110000->0
16110000-16115000->0
16115000-16120000->0
16120000-16125000->0
16125000-16130000->0
16130000-16135000->0
16135000-16140000->0
16140000-16145000->0
16145000-16150000->0
16150000-16155000->0
16155000-16160000->0
16160000-16165000->0
16165000-16170000->0
16170000-16175000->0
16175000-16180000->0
16180000-16185000->0
16185000-16190000->0
16190000-16195000->0
16195000-16200000->0
16200000-16205000->0
16205000-16210000->0
16210000-16215000->0
16215000-16220000->0
16220000-16225000->0
16225000-16230000->0
16230000-16235000->0
16235000-16240000->0
16240000-16245000->0
16245000-16250000->0
16250000-1625

26010000-26015000->0
26015000-26020000->0
26020000-26025000->0
26025000-26030000->0
26030000-26035000->0
26035000-26040000->0
26040000-26045000->0
26045000-26050000->0
26050000-26055000->0
26055000-26060000->0
26060000-26065000->0
26065000-26070000->0
26070000-26075000->0
26075000-26080000->0
26080000-26085000->0
26085000-26090000->0
26090000-26095000->0
26095000-26100000->0
26100000-26105000->0
26105000-26110000->0
26110000-26115000->0
26115000-26120000->0
26120000-26125000->0
26125000-26130000->0
26130000-26135000->0
26135000-26140000->0
26140000-26145000->0
26145000-26150000->0
26150000-26155000->0
26155000-26160000->0
26160000-26165000->0
26165000-26170000->0
26170000-26175000->0
26175000-26180000->0
26180000-26185000->0
26185000-26190000->0
26190000-26195000->0
26195000-26200000->0
26200000-26205000->0
26205000-26210000->0
26210000-26215000->0
26215000-26220000->0
26220000-26225000->0
26225000-26230000->0
26230000-26235000->0
26235000-26240000->0
26240000-26245000->0
26245000-2625

33975000-33980000->0
33980000-33985000->0
33985000-33990000->0
33990000-33995000->0
33995000-34000000->0
34000000-34005000->0
34005000-34010000->0
34010000-34015000->0
34015000-34020000->0
34020000-34025000->0
34025000-34030000->0
34030000-34035000->0
34035000-34040000->0
34040000-34045000->0
34045000-34050000->0
34050000-34055000->0
34055000-34060000->0
34060000-34065000->0
34065000-34070000->0
34070000-34075000->0
34075000-34080000->0
34080000-34085000->0
34085000-34090000->0
34090000-34095000->0
34095000-34100000->0
34100000-34105000->0
34105000-34110000->0
34110000-34115000->0
34115000-34120000->0
34120000-34125000->0
34125000-34130000->0
34130000-34135000->0
34135000-34140000->0
34140000-34145000->0
34145000-34150000->0
34150000-34155000->0
34155000-34160000->0
34160000-34165000->0
34165000-34170000->0
34170000-34175000->0
34175000-34180000->0
34180000-34185000->0
34185000-34190000->0
34190000-34195000->0
34195000-34200000->0
34200000-34205000->0
34205000-34210000->0
34210000-3421

...

459060000-459065000->0
459065000-459070000->0
459070000-459075000->0
459075000-459080000->0
459080000-459085000->0
459085000-459090000->0
459090000-459095000->0
459095000-459100000->0
459100000-459105000->0
459105000-459110000->0
459110000-459115000->0
459115000-459120000->0
459120000-459125000->0
459125000-459130000->0
459130000-459135000->0
459135000-459140000->0
459140000-459145000->0
459145000-459150000->0
459150000-459155000->0
459155000-459160000->0
459160000-459165000->0
459165000-459170000->0
459170000-459175000->0
459175000-459180000->0
459180000-459185000->0
459185000-459190000->0
459190000-459195000->0
459195000-459200000->0
459200000-459205000->0
459205000-459210000->0
459210000-459215000->0
459215000-459220000->0
459220000-459225000->0
459225000-459230000->0
459230000-459235000->0
459235000-459240000->0
459240000-459245000->0
459245000-459250000->0
459250000-459255000->0
459255000-459260000->0
459260000-459265000->0
459265000-459270000->0
459270000-459275000->0
459275000-4

468115000-468120000->0
468120000-468125000->0
468125000-468130000->0
468130000-468135000->0
468135000-468140000->0
468140000-468145000->0
468145000-468150000->0
468150000-468155000->0
468155000-468160000->0
468160000-468165000->0
468165000-468170000->0
468170000-468175000->0
468175000-468180000->0
468180000-468185000->0
468185000-468190000->0
468190000-468195000->0
468195000-468200000->0
468200000-468205000->0
468205000-468210000->0
468210000-468215000->0
468215000-468220000->0
468220000-468225000->0
468225000-468230000->0
468230000-468235000->0
468235000-468240000->0
468240000-468245000->0
468245000-468250000->0
468250000-468255000->0
468255000-468260000->0
468260000-468265000->0
468265000-468270000->0
468270000-468275000->0
468275000-468280000->0
468280000-468285000->0
468285000-468290000->0
468290000-468295000->0
468295000-468300000->0
468300000-468305000->0
468305000-468310000->0
468310000-468315000->0
468315000-468320000->0
468320000-468325000->0
468325000-468330000->0
468330000-4

475900000-475905000->0
475905000-475910000->0
475910000-475915000->0
475915000-475920000->0
475920000-475925000->0
475925000-475930000->0
475930000-475935000->0
475935000-475940000->0
475940000-475945000->0
475945000-475950000->0
475950000-475955000->0
475955000-475960000->0
475960000-475965000->0
475965000-475970000->0
475970000-475975000->0
475975000-475980000->0
475980000-475985000->0
475985000-475990000->0
475990000-475995000->0
475995000-476000000->0
476000000-476005000->0
476005000-476010000->0
476010000-476015000->0
476015000-476020000->0
476020000-476025000->0
476025000-476030000->0
476030000-476035000->0
476035000-476040000->0
476040000-476045000->0
476045000-476050000->0
476050000-476055000->0
476055000-476060000->0
476060000-476065000->0
476065000-476070000->0
476070000-476075000->0
476075000-476080000->0
476080000-476085000->0
476085000-476090000->0
476090000-476095000->0
476095000-476100000->0
476100000-476105000->0
476105000-476110000->0
476110000-476115000->0
476115000-4

484855000-484860000->0
484860000-484865000->0
484865000-484870000->0
484870000-484875000->0
484875000-484880000->0
484880000-484885000->0
484885000-484890000->0
484890000-484895000->0
484895000-484900000->0
484900000-484905000->0
484905000-484910000->0
484910000-484915000->0
484915000-484920000->0
484920000-484925000->0
484925000-484930000->0
484930000-484935000->0
484935000-484940000->0
484940000-484945000->0
484945000-484950000->0
484950000-484955000->0
484955000-484960000->0
484960000-484965000->0
484965000-484970000->0
484970000-484975000->0
484975000-484980000->0
484980000-484985000->0
484985000-484990000->0
484990000-484995000->0
484995000-485000000->0
485000000-485005000->0
485005000-485010000->0
485010000-485015000->0
485015000-485020000->0
485020000-485025000->0
485025000-485030000->0
485030000-485035000->0
485035000-485040000->0
485040000-485045000->0
485045000-485050000->0
485050000-485055000->0
485055000-485060000->0
485060000-485065000->0
485065000-485070000->0
485070000-4

493080000-493085000->0
493085000-493090000->0
493090000-493095000->0
493095000-493100000->0
493100000-493105000->0
493105000-493110000->0
493110000-493115000->0
493115000-493120000->0
493120000-493125000->0
493125000-493130000->0
493130000-493135000->0
493135000-493140000->0
493140000-493145000->0
493145000-493150000->0
493150000-493155000->0
493155000-493160000->0
493160000-493165000->0
493165000-493170000->0
493170000-493175000->0
493175000-493180000->0
493180000-493185000->0
493185000-493190000->0
493190000-493195000->0
493195000-493200000->0
493200000-493205000->0
493205000-493210000->0
493210000-493215000->0
493215000-493220000->0
493220000-493225000->0
493225000-493230000->0
493230000-493235000->0
493235000-493240000->0
493240000-493245000->0
493245000-493250000->0
493250000-493255000->0
493255000-493260000->0
493260000-493265000->0
493265000-493270000->0
493270000-493275000->0
493275000-493280000->0
493280000-493285000->0
493285000-493290000->0
493290000-493295000->0
493295000-4

In [328]:
#since most transactions have fees that are in the range 995000-1000000, I analyze this single range
#dividing this range into 50 ranges
limit = 1000000
step = int((limit - 995000) / 50)
min_limit_sub = 995000
max_limit_sub = min_limit_sub + step
value_index = 4
range_dict_sub = {}
while min_limit_sub < limit:
    key = str(min_limit_sub) + "-" + str(max_limit_sub)
    range_dict_sub[key] = 0
    for i in range(0, len(transactions_with_fees)):
        value = transactions_with_fees[i][value_index]
        if(min_limit_sub < value and value <= max_limit_sub):
            range_dict_sub[key] += 1
    
    min_limit_sub = max_limit_sub
    max_limit_sub += step

for key in range_dict_sub:
    print(str(key) + "->" + str(range_dict_sub.get(key)))

995000-995100->0
995100-995200->0
995200-995300->0
995300-995400->0
995400-995500->0
995500-995600->0
995600-995700->0
995700-995800->0
995800-995900->0
995900-996000->0
996000-996100->0
996100-996200->0
996200-996300->0
996300-996400->0
996400-996500->0
996500-996600->0
996600-996700->0
996700-996800->0
996800-996900->0
996900-997000->0
997000-997100->0
997100-997200->0
997200-997300->0
997300-997400->0
997400-997500->0
997500-997600->0
997600-997700->0
997700-997800->0
997800-997900->0
997900-998000->0
998000-998100->0
998100-998200->0
998200-998300->0
998300-998400->0
998400-998500->0
998500-998600->0
998600-998700->0
998700-998800->0
998800-998900->0
998900-999000->0
999000-999100->0
999100-999200->0
999200-999300->0
999300-999400->0
999400-999500->0
999500-999600->0
999600-999700->0
999700-999800->0
999800-999900->0
999900-1000000->1175


## 7) Propose one further analysis of your choice. Give a brief description of the analysis and report the results.


In [318]:

transactions_with_fees_df= pd.DataFrame(transactions_with_fees, columns = ['tx_id', 'block_id', 'input_value', 'output_value', 'fees'])

fees_per_block = (transactions_with_fees_df.groupby(['block_id'])['fees'].sum())
blocks_id_with_fees = fees_per_block.index.values.tolist() 
fees = fees_per_block.tolist()
blocks_fees_df = pd.DataFrame(list(zip(blocks_id_with_fees, fees )), columns = ['block_id', 'tot_fees'])
blocks_fees_df



block_id   tot_fees
0        2817  201000000
1       12986    3000000
2       14050   10000000
3       19867   14000000
4       20774   13000000
..        ...        ...
909     99959    5000000
910     99963    1000000
911     99989    5000000
912    100009    1000000
913    100016    3800000

[914 rows x 2 columns]

In [337]:
#write information aboute fees per block  in fees_block.csv file.
f = open('fees_block.csv', 'w')
writer = csv.writer(f)
header = ['block_id', 'tot_fees']
max_block_fee = 0
block_id_fees_max = 0
writer.writerow(header)
for i in range  (0,len(blocks_id_with_fees)):
    row = []
    block_id = blocks_id_with_fees[i]
    tot_fees = fees[i]
    row.append(block_id)
    row.append(tot_fees)
    writer.writerow(row)
    if tot_fees > max_block_fee:
        max_block_fee = tot_fees
        block_id_fees_max = block_id

f.close()

print("Block id with the highest total of fees: " + str(block_id_fees_max) + " with tot_fees: " + str(max_block_fee))
print("")

Block id with the highest total of fees: 75047 with tot_fees: 10000000000



In [344]:
limit = max_block_fee
step = int(limit / 10)
min_limit_sub = 0
max_limit_sub = step
range_dict_sub = {}
while min_limit_sub < limit:
    key = str(min_limit_sub) + "-" + str(max_limit_sub)
    range_dict_sub[key] = 0
    for i in range(0, len(fees)):
        value = fees[i]
        if(min_limit_sub < value and value <= max_limit_sub):
            range_dict_sub[key] += 1
            
    min_limit_sub = max_limit_sub
    max_limit_sub += step


for key in range_dict_sub:
    print(str(key) + "->" + str(range_dict_sub.get(key)))

0-1000000000->911
1000000000-2000000000->0
2000000000-3000000000->0
3000000000-4000000000->0
4000000000-5000000000->1
5000000000-6000000000->1
6000000000-7000000000->0
7000000000-8000000000->0
8000000000-9000000000->0
9000000000-10000000000->1


In [345]:
limit = 1000000000
step = int(limit / 10)
min_limit_sub = 0
max_limit_sub = step
range_dict_sub = {}
while min_limit_sub < limit:
    key = str(min_limit_sub) + "-" + str(max_limit_sub)
    range_dict_sub[key] = 0
    for i in range(0, len(fees)):
        value = fees[i]
        if(min_limit_sub < value and value <= max_limit_sub):
            range_dict_sub[key] += 1
            
    min_limit_sub = max_limit_sub
    max_limit_sub += step


for key in range_dict_sub:
    print(str(key) + "->" + str(range_dict_sub.get(key)))

0-100000000->899
100000000-200000000->7
200000000-300000000->3
300000000-400000000->0
400000000-500000000->1
500000000-600000000->0
600000000-700000000->1
700000000-800000000->0
800000000-900000000->0
900000000-1000000000->0


In [346]:
limit = 100000000
step = int(limit / 10)
min_limit_sub = 0
max_limit_sub = step
range_dict_sub = {}
while min_limit_sub < limit:
    key = str(min_limit_sub) + "-" + str(max_limit_sub)
    range_dict_sub[key] = 0
    for i in range(0, len(fees)):
        value = fees[i]
        if(min_limit_sub < value and value <= max_limit_sub):
            range_dict_sub[key] += 1
            
    min_limit_sub = max_limit_sub
    max_limit_sub += step


for key in range_dict_sub:
    print(str(key) + "->" + str(range_dict_sub.get(key)))

0-10000000->876
10000000-20000000->8
20000000-30000000->4
30000000-40000000->2
40000000-50000000->2
50000000-60000000->1
60000000-70000000->1
70000000-80000000->1
80000000-90000000->2
90000000-100000000->2


In [347]:
limit = 10000000
step = int(limit / 10)
min_limit_sub = 0
max_limit_sub = step
range_dict_sub = {}
while min_limit_sub < limit:
    key = str(min_limit_sub) + "-" + str(max_limit_sub)
    range_dict_sub[key] = 0
    for i in range(0, len(fees)):
        value = fees[i]
        if(min_limit_sub < value and value <= max_limit_sub):
            range_dict_sub[key] += 1
            
    min_limit_sub = max_limit_sub
    max_limit_sub += step


for key in range_dict_sub:
    print(str(key) + "->" + str(range_dict_sub.get(key)))

0-1000000->657
1000000-2000000->151
2000000-3000000->45
3000000-4000000->10
4000000-5000000->9
5000000-6000000->2
6000000-7000000->1
7000000-8000000->0
8000000-9000000->0
9000000-10000000->1


In [348]:
limit = 1000000
step = int(limit / 10)
min_limit_sub = 0
max_limit_sub = step
range_dict_sub = {}
while min_limit_sub < limit:
    key = str(min_limit_sub) + "-" + str(max_limit_sub)
    range_dict_sub[key] = 0
    for i in range(0, len(fees)):
        value = fees[i]
        if(min_limit_sub < value and value <= max_limit_sub):
            range_dict_sub[key] += 1
            
    min_limit_sub = max_limit_sub
    max_limit_sub += step


for key in range_dict_sub:
    print(str(key) + "->" + str(range_dict_sub.get(key)))

0-100000->31
100000-200000->2
200000-300000->7
300000-400000->2
400000-500000->6
500000-600000->2
600000-700000->2
700000-800000->6
800000-900000->5
900000-1000000->594
